In [14]:
import os
os.environ['PIP_CACHE_DIR'] = '/scratch/ola5/cache'
os.environ['HF_HOME'] = '/scratch/ola5/cache'

In [15]:
%cd Open-Sora-Plan

[Errno 2] No such file or directory: 'Open-Sora-Plan'
/scratch/ola5/opensora/Open-Sora-Plan


/scratch/ola5/opensora/lib/python3.10/site-packages/IPython/core/magics/osm.py:393: UserWarning: This is now an optional IPython functionality, using bookmarks requires you to install the `pickleshare` library.
  bkms = self.shell.db.get('bookmarks', {})


In [16]:
import torch

device = "cuda" if torch.cuda.is_available() else "cpu"
weight_dtype = torch.bfloat16

from PIL import Image
from torchvision import transforms
from torchvision.transforms import Lambda
from opensora.dataset.transform import ToTensorVideo, CenterCropResizeVideo, TemporalRandomCrop, LongSideResizeVideo, SpatialStrideCropVideo
import numpy as np
from einops import rearrange

from diffusers.schedulers import PNDMScheduler, EulerAncestralDiscreteScheduler
from transformers import T5EncoderModel, MT5EncoderModel, AutoTokenizer

from opensora.models.causalvideovae import ae_stride_config, ae_channel_config, ae_norm, ae_denorm, CausalVAEModelWrapper
from opensora.models.diffusion.opensora.modeling_inpaint import OpenSoraInpaint
from opensora.sample.pipeline_inpaint import OpenSoraInpaintPipeline

import imageio

In [4]:
vae = CausalVAEModelWrapper("./models/vae")
vae.vae = vae.vae.to(device=device, dtype=weight_dtype)
if True:
    vae.vae.enable_tiling()
    vae.vae.tile_overlap_factor = 0.125
    vae.vae.tile_sample_min_size = 256
    vae.vae.tile_latent_min_size = 32
    vae.vae.tile_sample_min_size_t = 29
    vae.vae.tile_latent_min_size_t = 8
vae.vae_scale_factor = ae_stride_config['CausalVAEModel_D4_4x8x8']

/scratch/ola5/opensora/lib/python3.10/site-packages/diffusers/configuration_utils.py:245: FutureWarning: It is deprecated to pass a pretrained model name or path to `from_config`.If you were trying to load a model, please use <class 'opensora.models.causalvideovae.model.causal_vae.modeling_causalvae.CausalVAEModel'>.load_config(...) followed by <class 'opensora.models.causalvideovae.model.causal_vae.modeling_causalvae.CausalVAEModel'>.from_config(...) instead. Otherwise, please make sure to pass a configuration dictionary instead. This functionality will be removed in v1.0.0.
  deprecate("config-passed-as-path", "1.0.0", deprecation_message, standard_warn=False)
The config attributes {'decoder_spatial_upsample_unup': ['', '', '', ''], 'encoder_spatial_downsample_undown': ['', '', '', ''], 'in_channels': 3, 'loss_params': {'disc_start': 1, 'disc_weight': 0.5, 'kl_weight': 1e-06, 'logvar_init': 0.0}, 'loss_type': 'opensora.models.ae.videobase.losses.LPIPSWithDiscriminator', 'lr': 1e-05, 

init from ./models/vae/checkpoint.ckpt
Load from normal model!


In [5]:
transformer_model = OpenSoraInpaint.from_pretrained("./models/93x480p_i2v", cache_dir='./cache_dir', low_cpu_mem_usage=False, device_map=None, torch_dtype=weight_dtype)

In [6]:
text_encoder = MT5EncoderModel.from_pretrained("./models/mt5-xxl", cache_dir='./cache_dir', low_cpu_mem_usage=False, torch_dtype=weight_dtype)
tokenizer = AutoTokenizer.from_pretrained("./models/mt5-xxl", cache_dir='./cache_dir')

/scratch/ola5/opensora/lib/python3.10/site-packages/torch/_utils.py:831: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  return self.fget.__get__(instance, owner)()
You are using the default legacy behaviour of the <class 'transformers.models.t5.tokenization_t5.T5Tokenizer'>. This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thoroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565
/scratch/ola5/opensora/lib/python3.10/site-packages/transformers/convert_slow_tokenizer.py:560: UserWarning: The sentencepiece tokeniz

In [7]:
transformer_model.eval()
vae.eval()
text_encoder.eval()
scheduler = PNDMScheduler()

In [8]:
pipeline = OpenSoraInpaintPipeline(vae=vae, text_encoder=text_encoder, tokenizer=tokenizer, scheduler=scheduler, transformer=transformer_model)
pipeline.to(device)

OpenSoraInpaintPipeline {
  "_class_name": "OpenSoraInpaintPipeline",
  "_diffusers_version": "0.28.0",
  "scheduler": [
    "diffusers",
    "PNDMScheduler"
  ],
  "text_encoder": [
    "transformers",
    "MT5EncoderModel"
  ],
  "tokenizer": [
    "transformers",
    "T5TokenizerFast"
  ],
  "transformer": [
    "opensora.models.diffusion.opensora.modeling_inpaint",
    "OpenSoraInpaint"
  ],
  "vae": [
    "opensora.models.causalvideovae.model.causal_vae",
    "CausalVAEModelWrapper"
  ]
}

In [22]:
images = ['./images/dock.jpg']

norm_fun = Lambda(lambda x: 2. * x - 1.)

resize = [CenterCropResizeVideo((480, 640)), ]
transform = transforms.Compose([
    ToTensorVideo(),
    *resize, 
    # RandomHorizontalFlipVideo(p=0.5),  # in case their caption have position decription
    norm_fun
])

def preprocess_images(images):
    print(images)
    if len(images) == 1:
        conditional_images_indices = [0]
    elif len(images) == 2:
        conditional_images_indices = [0, -1]
    else:
        print("Only support 1 or 2 condition images!")
        raise NotImplementedError
    
    try:
        conditional_images = [Image.open(image).convert("RGB") for image in images]
        conditional_images = [torch.from_numpy(np.copy(np.array(image))) for image in conditional_images]
        conditional_images = [rearrange(image, 'h w c -> c h w').unsqueeze(0) for image in conditional_images]
        conditional_images = [transform(image).to(device=device, dtype=weight_dtype) for image in conditional_images]
    except Exception as e:
        print('Error when loading images')
        print(f'condition images are {images}')
        raise e
    return dict(conditional_images=conditional_images, conditional_images_indices=conditional_images_indices)

pre_results = preprocess_images(images)
cond_imgs = pre_results['conditional_images']
cond_imgs_indices = pre_results['conditional_images_indices']

['./images/dock.jpg']


In [23]:
positive_prompt = """
(masterpiece), (best quality), (ultra-detailed),
{}.
"""
negative_prompt = """
lowres, bad anatomy, cropped, worst quality, low quality, jpeg artifacts, signature, watermark, username, blurry
"""
prompt = "Aerial view of docks with yachts and motorboats in Monaco"

#import pickle
#with open('prompt.pkl', 'rb') as f:
#    data = pickle.load(f)

num_frames = 93
videos = pipeline(
    conditional_images=cond_imgs,
    conditional_images_indices=cond_imgs_indices,
    prompt=positive_prompt.format(prompt),
    negative_prompt=negative_prompt,
    num_frames=num_frames,
    height=480,
    width=640,
    num_inference_steps=100,
    guidance_scale=7.5,
    num_images_per_prompt=1,
    mask_feature=True,
    device=device,
    max_sequence_length=300,
).images

conditional_images_indices: [0]


  0%|          | 0/100 [00:00<?, ?it/s]

In [24]:
videos.shape

torch.Size([1, 93, 480, 640, 3])

In [25]:
imageio.mimwrite("inpaint5.mp4", videos[0], fps=24, quality=8)

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [33]:
from IPython.display import HTML
from base64 import b64encode

mp4 = open('/scratch/ola5/opensora/Open-Sora-Plan/inpaint5.mp4','rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML("""
<video width=640 controls>
      <source src="%s" type="video/mp4">
</video>
""" % data_url)